In [1]:
import pandas as pd
from tqdm import tqdm
import subprocess

In [3]:
pytania = pd.read_csv("data/katalog_pytania_egzminacyjne_kandydat__14112024.csv")
pytania = pytania[pytania["Kategorie"].str.contains("A")]

In [6]:
result_df = pd.DataFrame(columns=["front", "back"])
for pytanie in tqdm(pytania.iloc):
    front = f"""<div class='question'>{pytanie.Pytanie}</div>"""

    if type(pytanie["Media"]) == str:
        media = pytanie["Media"].lower()
        front += "<div class='media'>"
        if media.endswith(".jpg"):
            front += f"""<img src='{pytanie["Media"]}' controls></img>"""
        elif pytanie["Media"].endswith(('.mp4','.wmv','.avi')):
            media = media.rsplit('.', 1)[0] + ".mp4"
            front += f"""[sound:{media}]"""
        else: 
            raise ValueError(f"Unsupported media type: {pytanie["Media"]}")
        front += "</div>"

    if type(pytanie["Odpowiedź A"]) == str:
        front += '<div class="odpowiedzi">'
        for l in ["A", "B", "C"]:
            if pytanie[f"Odpowiedź {l}"]:
                front += f'<span class="wariant">{l}</span>: {pytanie[f"Odpowiedź {l}"]}<br>'
        front +='</div>'

            

    back = f"""<div class='answer'>{pytanie["Poprawna odp"]}</div>"""

    result_df.loc[len(result_df)] = [front, back]


1592it [00:00, 3314.14it/s]


In [7]:
result_df.to_csv("data/anki_pytania.csv", index=False)

In [8]:
medias = list(filter(lambda x: type(x) is str, pytania["Media"].unique()))

In [9]:
pd.Series([x.split(".")[-1] for x in medias]).unique()

array(['wmv', 'jpg', 'JPG'], dtype=object)

In [20]:
for file in tqdm(medias):
    if file.endswith(".mp4"):
        continue
    if not file.endswith(".wmv"):
        subprocess.run([
            "cp", "media_temp/" + file, "media_processed/" + file
        ])
        continue
    input_file = f"media_temp/{file}"
    output_file = f"media_processed/{file.rsplit('.', 1)[0]}.mp4"

    subprocess.run([
        "ffmpeg",
        "-i", input_file,
        "-filter:v", "fps=30",
        "-c:v", "libx264",
        "-crf", "31",
        "-preset", "medium",
        "-movflags", "+faststart",
        "-an",
        output_file
    ])



  0%|          | 0/1333 [00:00<?, ?it/s]ffmpeg version 7.1 Copyright (c) 2000-2024 the FFmpeg developers
  built with Apple clang version 16.0.0 (clang-1600.0.26.4)
  configuration: --prefix=/opt/homebrew/Cellar/ffmpeg/7.1_4 --enable-shared --enable-pthreads --enable-version3 --cc=clang --host-cflags= --host-ldflags='-Wl,-ld_classic' --enable-ffplay --enable-gnutls --enable-gpl --enable-libaom --enable-libaribb24 --enable-libbluray --enable-libdav1d --enable-libharfbuzz --enable-libjxl --enable-libmp3lame --enable-libopus --enable-librav1e --enable-librist --enable-librubberband --enable-libsnappy --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtesseract --enable-libtheora --enable-libvidstab --enable-libvmaf --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx264 --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lzma --enable-libfontconfig --enable-libfreetype --enable-frei0r --enable-libass --enable-libopencore-amrnb --enable-libopencore-amrwb --